In [16]:
import os, sys
# sys.path.append('../src')
from copulae1 import *
from KDEs import *
from toolbox import *
import json
import datetime
import pickle
import matplotlib.pyplot as plt

from copulae1 import *
from KDEs import *
from toolbox import *
import toolbox
import scipy
from scipy import stats
from scipy.stats import norm
import pandas as pd
import numpy as np
import seaborn as sns
# from statsmodels.distributions.empirical_distribution import ECDF # don't use that
import os
np.random.seed(0)

import ray

try:
    ray.init(log_to_driver=True, num_cpus=10)
except RuntimeError:
    ray.shutdown()
#     ray.init(log_to_driver=False, runtime_env={'working_dir':'./'})
    ray.init(log_to_driver=True, num_cpus=10)

# !echo $PATH
Remember to remove path
'''
/Users/francis/Desktop/google-cloud-sdk/bin:/usr/local/mysql/bin:/Users/francis/bin:/Users/francis/opt/anaconda3/bin:/Users/francis/opt/anaconda3/condabin:/Users/francis/bin:/usr/local/bin:/usr/local/bin:/usr/bin:/bin:/usr/sbin:/sbin:/Applications/VMware Fusion.app/Contents/Public:/Library/TeX/texbin:/Library/Apple/usr/bin:/Users/francis/opt/anaconda3/bin
'''

In [17]:
spot_name = 'rs'
future_name = 'rf'

data_name = 'ETHUSD_BTCUSD_25SEP20'
data_path = '/Volumes/external_SSD/copulaData/Deribit_ready2/%s/'%data_name

ls = os.listdir(data_path + 'train/')
ls = [l for l in ls if l.endswith('.csv')]

with open(data_name+'_likelihood.pickle', 'rb') as f:
    likelihood_results = pickle.load(f)
    
with open(data_name+'_paras.pickle', 'rb') as f:
    paras_results = pickle.load(f)
    

In [18]:
# Risk Measure Specification
k_arr = [10] # Absolute risk aversion for exponential risk measure
q_arr_ES = [.01, .05] # Quantile level for expected shortfall
q_arr_VaR = [.01, .05] # Quantile level for Value at Risk

# To clip the h
min_h = 0
max_h = 20

# Gaussian, t_Copula, Clayton, Frank, Gumbel, Plackett, Gaussian mix Indep
C1 = Gaussian(dict(rho=0.9), Law_RS=stats.norm, Law_RF=stats.norm)  # fix the maringals!
C2 = t_Copula(dict(rho=0.1, nu=4), Law_RS=stats.norm, Law_RF=stats.norm, nu_lowerbound=2)
C2c = t_Copula(dict(rho=0.1, nu=4), Law_RS=stats.norm, Law_RF=stats.norm, nu_lowerbound=4)
C3 = Clayton(dict(theta=0.1), Law_RS=stats.norm, Law_RF=stats.norm)
C4 = Frank(dict(theta=0.1), Law_RS=stats.norm, Law_RF=stats.norm)
C5 = Gumbel(dict(theta=3), Law_RS=stats.norm, Law_RF=stats.norm)
C6 = Plackett(dict(theta=10), Law_RS=stats.norm, Law_RF=stats.norm)
C7 = Gaussian_Mix_Independent(dict(rho=.5, p=0.7), Law_RS=stats.norm, Law_RF=stats.norm)
C8 = rot180Gumbel(dict(theta=3), Law_RS=stats.norm, Law_RF=stats.norm)

Copulae_names = ['Gaussian', 't_Copula', 't_Copula_Capped', 'Clayton', 'Frank', 'Gumbel', 'Plackett', 'Gauss Mix Indep', 'rotGumbel']
Copulae_arr = [C1, C2, C2c, C3, C4, C5, C6, C7, C8]
Copulae = dict(zip(Copulae_names, Copulae_arr))

In [19]:
# Prettify the result
c_arr = []
date_range_arr = []
for i, file in enumerate(ls):
	train = pd.read_csv(data_path + 'train/' + file)
	date_range = train.datetime.iloc[-1] + ' to ' + train.datetime.iloc[0]
	date_range_arr.append(date_range)

	c = pd.DataFrame(paras_results[file])
	c.index = c.iloc[:, 0]
	c = pd.DataFrame(c.iloc[:, 1])
	c_arr.append(c)

paras_results_pd = pd.concat(dict(zip(ls, c_arr)), axis=1)
paras_results_pd.columns = paras_results_pd.columns.droplevel(1)
paras_results_pd.index.name = None

l_arr = []
date_range_arr = []
for i, file in enumerate(list(paras_results_pd.columns)):
	train = pd.read_csv(data_path + 'train/' + file)
	date_range = train.datetime.iloc[-1] + ' to ' + train.datetime.iloc[0]
	date_range_arr.append(date_range)

	c = pd.DataFrame(likelihood_results[file])
	c.index = c.iloc[:, 0]
	c = pd.DataFrame(c.iloc[:, 1])
	l_arr.append(c)

likelihood_results_pd = pd.concat(dict(zip(ls, l_arr)), axis=1)
likelihood_results_pd.columns = likelihood_results_pd.columns.droplevel(1)
likelihood_results_pd.index.name = None

In [20]:
paras = paras_results_pd.copy()
assert len(ls) == len(paras.columns)

In [21]:
data_name

'ETHUSD_BTCUSD_25SEP20'

In [22]:
def getOHR(file):
    print('-----', file, len(ls), str(datetime.datetime.now()), '-----')
    train = pd.read_csv(data_path + 'train/' + file)
    spot = train.loc[:, spot_name]
    future = train.loc[:, future_name]
    u = ECDF(spot)(spot)
    v = ECDF(future)(future)

    kde_brr = KDE(spot, "Gaussian")
    kde_btc = KDE(future, "Gaussian")

    # load paras
    for C_name in Copulae:
        p = paras.loc[C_name, file]
        if (C_name == 't_Copula') or (C_name == 't_Copula_Capped'):
            Copulae[C_name].__init__(p, kde_brr, kde_btc, nu_lowerbound=2)
        else:
            Copulae[C_name].__init__(p, kde_brr, kde_btc)

        print(C_name, Copulae[C_name].paras)

    # Get Best h
    best_h = []
    for C_name in Copulae:
        np.random.seed(0)
        best_h.append(optimize_h(Copulae[C_name], k_arr, q_arr_ES, q_arr_VaR))
    best_h = pd.DataFrame(best_h)
    best_h.columns = ['Variance'] + ['ERM k=%i' % k for k in k_arr] + ['ES q=%.2f' % q for q in q_arr_ES] + [
        'VaR q=%.2f' % q for q in q_arr_VaR]
    best_h.index = Copulae_names
    
    with open('best_h/'+data_name+'/%s'%file+'_best_h.pickle', 'wb') as f:
        pickle.dump(best_h, f)
        print('saved')

@ray.remote
def getOHR_parallel(file):
#     print('start', file)
    getOHR(file)

In [32]:
getOHR('172.csv')

----- 172.csv 186 2022-10-27 14:34:19.930778 -----
Gaussian {'rho': 0.7916051407595548}
t_Copula {'rho': 0.6883627074838385, 'nu': 2.0000000000004805}
t_Copula_Capped {'rho': 0.7388899838136624, 'nu': 4.000000000000177}
Clayton {'theta': 2.087574349623334}
Frank {'theta': 12.697812926579726}
Gumbel {'theta': 2.2854731689398573}
Plackett {'theta': 26.529273995410133}
Gauss Mix Indep {'rho': 0.9721890721486942, 'p': 0.6290592359334248}
rotGumbel {'theta': 2.259125657756649}
Optimization terminated successfully.
         Current function value: 0.000029
         Iterations: 12
         Function evaluations: 24
Optimization terminated successfully.
         Current function value: 0.007216
         Iterations: 12
         Function evaluations: 24
Optimization terminated successfully.
         Current function value: 0.016719
         Iterations: 13
         Function evaluations: 26
Optimization terminated successfully.
         Current function value: 0.011786
         Iterations: 11
     

/Users/francis/Google Drive/00_IRTG1792/copula/revision/toolbox.py:294: RuntimeWarning: invalid value encountered in power
  part2 = np.sin(self.alpha * (U + xi)) / (np.cos(U) ** (1 / self.alpha))
/Users/francis/Google Drive/00_IRTG1792/copula/revision/toolbox.py:295: RuntimeWarning: invalid value encountered in power
  part3 = (np.cos(U - self.alpha * (U + xi)) / W) ** ((1 - self.alpha) / self.alpha)


Optimization terminated successfully.
         Current function value: 0.000025
         Iterations: 13
         Function evaluations: 26
Optimization terminated successfully.
         Current function value: 0.007495
         Iterations: 10
         Function evaluations: 20
Optimization terminated successfully.
         Current function value: 0.017940
         Iterations: 11
         Function evaluations: 22
Optimization terminated successfully.
         Current function value: 0.012516
         Iterations: 12
         Function evaluations: 24
Optimization terminated successfully.
         Current function value: 0.015547
         Iterations: 12
         Function evaluations: 28
Optimization terminated successfully.
         Current function value: 0.007775
         Iterations: 11
         Function evaluations: 23
Optimization terminated successfully.
         Current function value: 0.000037
         Iterations: 10
         Function evaluations: 20
Optimization terminated successful

In [43]:
file = '167.csv'
with open('best_h/'+data_name+'/%s'%file+'_best_h.pickle', 'rb') as f:
    a = pickle.load(f)
    
a

Variance  ERM k=10  ES q=0.01  ES q=0.05  VaR q=0.01  \
Gaussian         1.145215  0.885352   0.765625   0.908594    1.009766   
t_Copula         1.074902  0.891895   0.449414   0.881152    0.801562   
t_Copula_Capped  1.134961  0.901074   0.658594   0.906055    0.967480   
Clayton          0.772559  0.648633   0.482617   0.677441    0.656250   
Frank            0.983008  0.766602   0.587500   0.751074    0.906445   
Gumbel           1.233984  1.049512   1.090625   1.106250    1.132910   
Plackett         0.985059  0.767480   0.547070   0.750586    0.800977   
Gauss Mix Indep  0.971680  0.779590   0.379492   0.712891    0.501270   
rotGumbel        1.005762  0.798340   0.589746   0.811719    0.865430   

                 VaR q=0.05  
Gaussian           0.929883  
t_Copula           1.048730  
t_Copula_Capped    1.033496  
Clayton            1.015625  
Frank              0.672559  
Gumbel             1.035156  
Plackett           0.775879  
Gauss Mix Indep    1.132812  
rotGumbel          1.033594

In [41]:
paras.loc['t_Copula', file]

{'rho': 0.6854981372406179, 'nu': 2.4627295120368013}

In [42]:
paras.loc['t_Copula_Capped', file]

{'rho': 0.7193048687303403, 'nu': 4.000000000000716}

In [23]:
savePath = 'best_h/'+data_name
done = [l for l in os.listdir(savePath) if l.endswith('pickle')]
done = set([l[:l.find('.csv')+4] for l in done ])
# to_run =  sorted(list(set(ls) - done))
to_run =  sorted(list(set(ls)))


print(len(to_run), savePath)

186 best_h/ETHUSD_BTCUSD_25SEP20


In [33]:
OHRs = ray.get([getOHR_parallel.remote(file) for file in to_run])

(getOHR_parallel pid=99435) ----- 103.csv 186 2022-09-23 16:33:39.546273 -----
(getOHR_parallel pid=99434) ----- 104.csv 186 2022-09-23 16:33:39.546343 -----
(getOHR_parallel pid=99440) ----- 10.csv 186 2022-09-23 16:33:39.538020 -----
(getOHR_parallel pid=99437) ----- 106.csv 186 2022-09-23 16:33:39.538767 -----
(getOHR_parallel pid=99443) ----- 0.csv 186 2022-09-23 16:33:39.539404 -----
(getOHR_parallel pid=99438) ----- 101.csv 186 2022-09-23 16:33:39.544717 -----
(getOHR_parallel pid=99436) ----- 105.csv 186 2022-09-23 16:33:39.553242 -----
(getOHR_parallel pid=99441) ----- 102.csv 186 2022-09-23 16:33:39.538022 -----
(getOHR_parallel pid=99439) ----- 100.csv 186 2022-09-23 16:33:39.549299 -----
(getOHR_parallel pid=99442) ----- 1.csv 186 2022-09-23 16:33:39.540041 -----
(getOHR_parallel pid=99435) Gaussian {'rho': 0.9672100618253597}
(getOHR_parallel pid=99435) t_Copula {'rho': 0.947904531379516, 'nu': 2.0000000000001177}
(getOHR_parallel pid=99435) t_Copula_Capped {'rho': 0.957401

(getOHR_parallel pid=99443) Optimization terminated successfully.
(getOHR_parallel pid=99443)          Current function value: 0.000002
(getOHR_parallel pid=99443)          Iterations: 12
(getOHR_parallel pid=99443)          Function evaluations: 24
(getOHR_parallel pid=99438) Optimization terminated successfully.
(getOHR_parallel pid=99438)          Current function value: 0.000001
(getOHR_parallel pid=99438)          Iterations: 11
(getOHR_parallel pid=99438)          Function evaluations: 22
(getOHR_parallel pid=99435) Optimization terminated successfully.
(getOHR_parallel pid=99435)          Current function value: 0.000001
(getOHR_parallel pid=99435)          Iterations: 11
(getOHR_parallel pid=99435)          Function evaluations: 22
(getOHR_parallel pid=99441) Optimization terminated successfully.
(getOHR_parallel pid=99441)          Current function value: 0.000001
(getOHR_parallel pid=99441)          Iterations: 11
(getOHR_parallel pid=99441)          Function evaluations: 22


(getOHR_parallel pid=99434) Optimization terminated successfully.
(getOHR_parallel pid=99434)          Current function value: 0.003500
(getOHR_parallel pid=99434)          Iterations: 13
(getOHR_parallel pid=99434)          Function evaluations: 26
(getOHR_parallel pid=99441) Optimization terminated successfully.
(getOHR_parallel pid=99441)          Current function value: 0.003491
(getOHR_parallel pid=99441)          Iterations: 13
(getOHR_parallel pid=99441)          Function evaluations: 26
(getOHR_parallel pid=99436) Optimization terminated successfully.
(getOHR_parallel pid=99436)          Current function value: 0.003591
(getOHR_parallel pid=99436)          Iterations: 13
(getOHR_parallel pid=99436)          Function evaluations: 26
(getOHR_parallel pid=99443) Optimization terminated successfully.
(getOHR_parallel pid=99443)          Current function value: 0.002749
(getOHR_parallel pid=99443)          Iterations: 11
(getOHR_parallel pid=99443)          Function evaluations: 22


(getOHR_parallel pid=99434) Optimization terminated successfully.
(getOHR_parallel pid=99434)          Current function value: 0.001011
(getOHR_parallel pid=99434)          Iterations: 12
(getOHR_parallel pid=99434)          Function evaluations: 26
(getOHR_parallel pid=99441) Optimization terminated successfully.
(getOHR_parallel pid=99441)          Current function value: 0.000983
(getOHR_parallel pid=99441)          Iterations: 13
(getOHR_parallel pid=99441)          Function evaluations: 27
(getOHR_parallel pid=99442) Optimization terminated successfully.
(getOHR_parallel pid=99442)          Current function value: 0.000002
(getOHR_parallel pid=99442)          Iterations: 12
(getOHR_parallel pid=99442)          Function evaluations: 24
(getOHR_parallel pid=99439) Optimization terminated successfully.
(getOHR_parallel pid=99439)          Current function value: 0.000001
(getOHR_parallel pid=99439)          Iterations: 12
(getOHR_parallel pid=99439)          Function evaluations: 24


(getOHR_parallel pid=99439) Optimization terminated successfully.
(getOHR_parallel pid=99439)          Current function value: 0.002454
(getOHR_parallel pid=99439)          Iterations: 11
(getOHR_parallel pid=99439)          Function evaluations: 24
(getOHR_parallel pid=99437) Optimization terminated successfully.
(getOHR_parallel pid=99437)          Current function value: 0.003860
(getOHR_parallel pid=99437)          Iterations: 13
(getOHR_parallel pid=99437)          Function evaluations: 26
(getOHR_parallel pid=99435) Optimization terminated successfully.
(getOHR_parallel pid=99435)          Current function value: 0.003650
(getOHR_parallel pid=99435)          Iterations: 13
(getOHR_parallel pid=99435)          Function evaluations: 26
(getOHR_parallel pid=99443) Optimization terminated successfully.
(getOHR_parallel pid=99443)          Current function value: 0.002779
(getOHR_parallel pid=99443)          Iterations: 11
(getOHR_parallel pid=99443)          Function evaluations: 22


...

(getOHR_parallel pid=99441) Optimization terminated successfully.
(getOHR_parallel pid=99441)          Current function value: 0.001169
(getOHR_parallel pid=99441)          Iterations: 11
(getOHR_parallel pid=99441)          Function evaluations: 22
(getOHR_parallel pid=99437) Optimization terminated successfully.
(getOHR_parallel pid=99437)          Current function value: 0.001730
(getOHR_parallel pid=99437)          Iterations: 11
(getOHR_parallel pid=99437)          Function evaluations: 22
(getOHR_parallel pid=99441) Optimization terminated successfully.
(getOHR_parallel pid=99441)          Current function value: 0.003724
(getOHR_parallel pid=99441)          Iterations: 12
(getOHR_parallel pid=99441)          Function evaluations: 24
(getOHR_parallel pid=99437) Optimization terminated successfully.
(getOHR_parallel pid=99437)          Current function value: 0.002126
(getOHR_parallel pid=99437)          Iterations: 10
(getOHR_parallel pid=99437)          Function evaluations: 23


(getOHR_parallel pid=99439) Optimization terminated successfully.
(getOHR_parallel pid=99439)          Current function value: 0.002782
(getOHR_parallel pid=99439)          Iterations: 13
(getOHR_parallel pid=99439)          Function evaluations: 26
(getOHR_parallel pid=99443) Optimization terminated successfully.
(getOHR_parallel pid=99443)          Current function value: 0.000001
(getOHR_parallel pid=99443)          Iterations: 12
(getOHR_parallel pid=99443)          Function evaluations: 24
(getOHR_parallel pid=99439) Optimization terminated successfully.
(getOHR_parallel pid=99439)          Current function value: 0.003734
(getOHR_parallel pid=99439)          Iterations: 15
(getOHR_parallel pid=99439)          Function evaluations: 31
(getOHR_parallel pid=99440) Optimization terminated successfully.
(getOHR_parallel pid=99440)          Current function value: 0.000001
(getOHR_parallel pid=99440)          Iterations: 12
(getOHR_parallel pid=99440)          Function evaluations: 24


(getOHR_parallel pid=99440) Optimization terminated successfully.
(getOHR_parallel pid=99440)          Current function value: 0.003205
(getOHR_parallel pid=99440)          Iterations: 11
(getOHR_parallel pid=99440)          Function evaluations: 25
(getOHR_parallel pid=99442) Optimization terminated successfully.
(getOHR_parallel pid=99442)          Current function value: 0.003395
(getOHR_parallel pid=99442)          Iterations: 10
(getOHR_parallel pid=99442)          Function evaluations: 21
(getOHR_parallel pid=99440) Optimization terminated successfully.
(getOHR_parallel pid=99440)          Current function value: 0.000959
(getOHR_parallel pid=99440)          Iterations: 12
(getOHR_parallel pid=99440)          Function evaluations: 26
(getOHR_parallel pid=99442) Optimization terminated successfully.
(getOHR_parallel pid=99442)          Current function value: 0.000995
(getOHR_parallel pid=99442)          Iterations: 12
(getOHR_parallel pid=99442)          Function evaluations: 28


(getOHR_parallel pid=99442) Optimization terminated successfully.
(getOHR_parallel pid=99442)          Current function value: 0.001542
(getOHR_parallel pid=99442)          Iterations: 12
(getOHR_parallel pid=99442)          Function evaluations: 24
(getOHR_parallel pid=99443) Optimization terminated successfully.
(getOHR_parallel pid=99443)          Current function value: 0.002900
(getOHR_parallel pid=99443)          Iterations: 12
(getOHR_parallel pid=99443)          Function evaluations: 24
(getOHR_parallel pid=99440) Optimization terminated successfully.
(getOHR_parallel pid=99440)          Current function value: 0.005654
(getOHR_parallel pid=99440)          Iterations: 14
(getOHR_parallel pid=99440)          Function evaluations: 28
(getOHR_parallel pid=99437) Optimization terminated successfully.
(getOHR_parallel pid=99437)          Current function value: 0.000001
(getOHR_parallel pid=99437)          Iterations: 12
(getOHR_parallel pid=99437)          Function evaluations: 24


(getOHR_parallel pid=99437) Optimization terminated successfully.
(getOHR_parallel pid=99437)          Current function value: 0.001841
(getOHR_parallel pid=99437)          Iterations: 13
(getOHR_parallel pid=99437)          Function evaluations: 27
(getOHR_parallel pid=99441) Optimization terminated successfully.
(getOHR_parallel pid=99441)          Current function value: 0.001825
(getOHR_parallel pid=99441)          Iterations: 13
(getOHR_parallel pid=99441)          Function evaluations: 26
(getOHR_parallel pid=99437) Optimization terminated successfully.
(getOHR_parallel pid=99437)          Current function value: 0.000824
(getOHR_parallel pid=99437)          Iterations: 13
(getOHR_parallel pid=99437)          Function evaluations: 27
(getOHR_parallel pid=99437) saved
(getOHR_parallel pid=99441) Optimization terminated successfully.
(getOHR_parallel pid=99441)          Current function value: 0.002103
(getOHR_parallel pid=99441)          Iterations: 14
(getOHR_parallel pid=99441) 

In [ ]:
# Placeholders for results
best_h_results = []

for num, file in enumerate(list(paras.columns)):
    print('-----', num, len(ls), str(datetime.datetime.now()), '-----')
    train = pd.read_csv(data_path + 'train/' + file)
    spot = train.loc[:, spot_name]
    future = train.loc[:, future_name]
    u = ECDF(spot)(spot)
    v = ECDF(future)(future)

    kde_brr = KDE(spot, "Gaussian")
    kde_btc = KDE(future, "Gaussian")

    # load paras
    for C_name in Copulae:
        p = paras.loc[C_name, file]
        if (C_name == 't_Copula') or (C_name == 't_Copula_Capped'):
            Copulae[C_name].__init__(p, kde_brr, kde_btc, nu_lowerbound=2)
        else:
            Copulae[C_name].__init__(p, kde_brr, kde_btc)

        print(C_name, Copulae[C_name].paras)

    # Get Best h
    best_h = []
    for C_name in Copulae:
        np.random.seed(0)
        best_h.append(optimize_h(Copulae[C_name], k_arr, q_arr_ES, q_arr_VaR))
    best_h = pd.DataFrame(best_h)
    best_h.columns = ['Variance'] + ['ERM k=%i' % k for k in k_arr] + ['ES q=%.2f' % q for q in q_arr_ES] + [
        'VaR q=%.2f' % q for q in q_arr_VaR]
    best_h.index = Copulae_names
    best_h_results.append(best_h)
    
    if (num%60==0) or (num == 0) or (num==len(ls)):
        print('saved!')
        with open(data_name+'_best_h.pickle', 'wb') as f:
            pickle.dump(best_h_results, f)

best_h_results_pd = pd.concat(dict(zip(list(paras.columns), best_h_results)), axis=1)
best_h_results_pd.apply(lambda x: np.clip(x, min_h, max_h))
with open(data_name+'_best_h.pickle', 'wb') as f:
    pickle.dump(best_h_results_pd, f)

In [ ]:
pd.concat(best_h_results)

In [ ]:
len(best_h_results)

In [ ]:
likelihood_results_pd.mean(axis=1)